# Data Conversion of 9/11plus .hex data
This python notebook shows how to convert a .hex file into pandas dataframe with scientific values.

Please contact [SBS customer support](https://www.seabird.com/support) for help or to request additional features.

Example data provided by CalCOFI. Station Santa Barbara Basin

## Init

The initialization code section below is used to import required libraries.

In [1]:
# Native imports
import os
import sys
import gsw
sys.path.append(os.path.abspath(".."))

# Third-party imports
import numpy as np
import pandas as pd

# Sea-Bird imports
import seabirdscientific.conversion as conv
import seabirdscientific.instrument_data as id
import seabirdscientific.visualization as viz
import resources.example_coefficients as ec

## [Data Conversion](#proc-list)

This section shows how to convert raw data contained in a .hex file into scientific units for the instruments that follow:  
- 9/11plus

In [ ]:
hex_file = os.path.join("..","resources", "test-data", "SBE911plus", "2507054.hex")

# Convert raw hexadecimal string to raw frequencies
raw_data = id.read_hex_file(
    filepath=hex_file,
    instrument_type=id.InstrumentType.SBE911Plus,
    enabled_sensors=[
        id.Sensors.Temperature,
        id.Sensors.Conductivity,
        id.Sensors.Pressure,
        id.Sensors.SecondaryTemperature,
        id.Sensors.SecondaryConductivity,
        id.Sensors.ExtVolt0,
        id.Sensors.ExtVolt1,
        id.Sensors.ExtVolt2,
        id.Sensors.ExtVolt3,
        id.Sensors.ExtVolt4,
        id.Sensors.ExtVolt5,
        id.Sensors.ExtVolt6,
        id.Sensors.ExtVolt7,
        id.Sensors.SPAR,
        id.Sensors.nmeaLocation,
        id.Sensors.SystemTime
    ],
    frequency_channels_suppressed=0,
    voltage_words_suppressed=0
)

temperature  conductivity  digiquartz pressure  secondary temperature  \
0      4651.167969   6638.984375         33302.257812            4651.781250   
1      4650.960938   6638.968750         33302.250000            4651.718750   
2      4650.218750   6638.941406         33302.230469            4651.750000   
3      4649.523438   6638.867188         33302.285156            4651.769531   
4      4649.417969   6638.757812         33302.250000            4651.945312   
...            ...           ...                  ...                    ...   
48686  4654.687500   6641.460938         33302.316406            4656.417969   
48687  4654.593750   6641.429688         33302.308594            4656.449219   
48688  4654.429688   6641.394531         33302.316406            4656.500000   
48689  4654.429688   6641.398438         33302.316406            4656.515625   
48690  4654.238281   6641.347656         33302.308594            4656.613281   

       secondary conductivity    volt 0    volt 1    volt 2    volt 3  \
0                 6230.480469  3.733822  0.211233  4.932845  2.336996   
1                 6230.503906  3.735043  0.211233  4.932845  2.340659   
2                 6230.519531  3.736264  0.211233  4.932845  2.356532   
3                 6230.535156  3.736264  0.213675  4.932845  2.379731   
4                 6230.535156  3.736264  0.214896  4.932845  2.385836   
...                       ...       ...       ...       ...       ...   
48686             6233.207031  3.693529  0.268620  4.932845  2.432234   
48687             6233.234375  3.692308  0.268620  4.932845  2.423687   
48688             6233.292969  3.692308  0.268620  4.932845  2.421245   
48689             6233.308594  3.692308  0.268620  4.932845  2.415140   
48690             6233.343750  3.692308  0.268620  4.932845  2.400488   

         volt 4  ...  surface par  NMEA Latitude  NMEA Longitude  \
0      2.488400  ...     1.431013       34.27570       -120.0256   
1      2.488400  ...     1.431013       34.27570       -120.0256   
2      2.488400  ...     1.431013       34.27570       -120.0256   
3      2.487179  ...     1.431013       34.27570       -120.0256   
4      2.488400  ...     1.431013       34.27570       -120.0256   
...         ...  ...          ...            ...             ...   
48686  2.509158  ...     1.345543       34.27568       -120.0256   
48687  2.510379  ...     1.345543       34.27568       -120.0256   
48688  2.509158  ...     1.345543       34.27568       -120.0256   
48689  2.510379  ...     1.345543       34.27568       -120.0256   
48690  2.509158  ...     1.345543       34.27568       -120.0256   

       temperature compensation  SBE911 pump status  \
0                        2498.0                 0.0   
1                        2499.0                 0.0   
2                        2498.0                 0.0   
3                        2499.0                 0.0   
4                        2499.0                 0.0   
...                         ...                 ...   
48686                    2410.0                 0.0   
48687                    2410.0                 0.0   
48688                    2410.0                 0.0   
48689                    2410.0                 0.0   
48690                    2410.0                 0.0   

       SBE911 bottom contact status  SBE911 confirm status  \
0                               0.0                    1.0   
1                               0.0                    1.0   
2                               0.0                    1.0   
3                               0.0                    1.0   
4                               0.0                    1.0   
...                             ...                    ...   
48686                           0.0                    1.0   
48687                           0.0                    1.0   
48688                           0.0                    1.0   
48689                           0.0                    1.0   
48690    

In [ ]:
# Convert raw frequencies to scientific values
sample_interval = 1/24

temperature = conv.convert_temperature_frequency(
    frequency=raw_data["temperature"].values,
    coefs=ec.temperature_coefs_sn5102,
    standard='ITS90',
    units='C',
)

pressure = conv.convert_pressure_digiquartz(
    pressure_count=raw_data["digiquartz pressure"].values,
    compensation_voltage=raw_data["temperature compensation"],
    coefs=ec.pressure_coefs_sn0936,
    units='psia',
    sample_interval= sample_interval
)

conductivity = conv.convert_conductivity(
    conductivity_count=raw_data["conductivity"].values,
    temperature=temperature,
    pressure=pressure,
    coefs=ec.conductivity_coefs_sn3569,
    scalar=0.1
)

secondary_temperature = conv.convert_temperature_frequency(
    frequency=raw_data["temperature"].values,
    coefs=ec.temperature_coefs_sn5109,
    standard='ITS90',
    units='C',
)

secondary_conductivity = conv.convert_conductivity(
    conductivity_count=raw_data["conductivity"].values,
    temperature=temperature,
    pressure=pressure,
    coefs=ec.conductivity_coefs_sn2206,
    scalar=0.1
)

# Salinity
salinity = gsw.SP_from_C(
    C=conductivity,
    t=temperature,
    p=pressure
)

chlorophyll = conv.convert_eco(
    raw = raw_data["volt 1"],
    coefs = ec.chlorophyll_a_coefs_sn3122
)

# TODO: Altimeter

oxygen = conv.convert_sbe43_oxygen(
    voltage = raw_data["volt 4"],
    temperature=temperature,
    pressure=pressure,
    salinity=salinity,
    coefs=ec.oxygen_43_coefs_sn1590,
    apply_tau_correction=True,
    apply_hysteresis_correction=True,
    window_size =1,
    sample_interval=sample_interval
)

oxygen_secondary = conv.convert_sbe43_oxygen(
    voltage = raw_data["volt 5"],
    temperature=temperature,
    pressure=pressure,
    salinity=salinity,
    coefs=ec.oxygen_43_coefs_sn0680,
    apply_tau_correction=True,
    apply_hysteresis_correction=True,
    window_size =1,
    sample_interval=1/24
)

ph = conv.convert_sbe18_ph(
    raw_ph = raw_data["volt 7"],
    temperature=temperature,
    coefs=ec.ph_coefs_sn0709
)

# TODO: SPAR

# Flag to be used in data processing
flag = np.zeros(len(temperature))

data = pd.DataFrame({
    "temp": temperature,
    "cond":conductivity,
    "press":pressure,
    "temp_secondary": secondary_temperature,
    "cond_secondary":secondary_conductivity,
    "chlorophyll": chlorophyll,
    "oxygen":oxygen,
    "oxygen_secondary":oxygen_secondary,
    "ph":ph,
    "nmea_lat":raw_data["NMEA Latitude"],
    "nmea_long":raw_data["NMEA Longitude"],
    "pump_status":raw_data["SBE911 pump status"],
    "bottom_contact":raw_data["SBE911 bottom contact status"],
    "confirm_status":raw_data["SBE911 confirm status"],
    "modem_status":raw_data["SBE911 modem status"],
    "system_time":raw_data["system time"],
    "data_integrity":raw_data["data integrity"],
    "flag":flag
})

data

temp      cond     press  temp_secondary  cond_secondary  \
0      16.679901  4.298926  6.613337       16.672640        5.019316   
1      16.677698  4.298901  6.593769       16.670445        5.019288   
2      16.669802  4.298858  6.544885       16.662573        5.019238   
3      16.662404  4.298739  6.681747       16.655198        5.019103   
4      16.661282  4.298564  6.593741       16.654079        5.018904   
...          ...       ...       ...             ...             ...   
48686  16.717332  4.302886  7.633291       16.709954        5.023823   
48687  16.716335  4.302836  7.613795       16.708960        5.023766   
48688  16.714590  4.302780  7.633407       16.707221        5.023702   
48689  16.714590  4.302786  7.633464       16.707221        5.023709   
48690  16.712555  4.302705  7.613968       16.705192        5.023616   

       chlorophyll    oxygen  oxygen_secondary        ph  nmea_lat  nmea_long  \
0         2.252032  7.594037          7.044956  7.863271  34.27570  -120.0256   
1         2.252032  7.594311          7.049200  7.863277  34.27570  -120.0256   
2         2.252032  7.595310          7.050318  7.863301  34.27570  -120.0256   
3         2.283778  7.591690          7.051528  7.863323  34.27570  -120.0256   
4         2.299651  7.596492          7.051621  7.863326  34.27570  -120.0256   
...            ...       ...               ...       ...       ...        ...   
48686     2.998063  7.670289          7.071722  7.815516  34.27568  -120.0256   
48687     2.998063  7.675132          7.071853  7.815519  34.27568  -120.0256   
48688     2.998063  7.670658          7.072129  7.815523  34.27568  -120.0256   
48689     2.998063  7.675385          7.072129  7.815523  34.27568  -120.0256   
48690     2.998063  7.670913          7.072414  7.815529  34.27568  -120.0256   

       pump_status  bottom_contact  confirm_status  modem_status  \
0              0.0             0.0             1.0           1.0   
1              0.0             0.0             1.0           1.0   
2              0.0             0.0             1.0           1.0   
3              0.0             0.0             1.0           1.0   
4              0.0             0.0             1.0           1.0   
...            ...             ...             ...           ...   
48686          0.0             0.0             1.0           1.0   
48687          0.0             0.0             1.0           1.0   
48688          0.0             0.0             1.0           1.0   
48689          0.0             0.0             1.0           1.0   
48690          0.0             0.0             1.0           1.0   

              system_time  data_integrity  
0     2025-07-28 23:43:53            83.0  
1     2025-07-28 23:43:53            84.0  
2     2025-07-28 23:43:53            85.0  
3     2025-07-28 23:43:53            86.0  
4     2025-07-28 23:43:53            87.0  
...                   ...             ...  
48686 2025-07-29 00:17:42           129.0  
48687 2025-07-29 00:17:42           130.0  
48688 2025-07-29 00:17:42           131.0  
48689 2025-07-29 00:17:42           132.0  
48690 2025-07-29 00:17:42           133.0  

[48691 rows x 17 columns]

## [Data Plotting](#proc-list)

In [19]:
config = viz.ChartConfig(
    title="9/11plus Data Conversion",
    x_names=["temp", "cond", "chlorophyll", "oxygen"],
    y_names=["press"],
    z_names=[],
    chart_type="overlay",
    plot_loop_edit_flags=False,
    lift_pen_over_bad_data=True,
)

chart_data = viz.ChartData(data, config)
fig = viz.plot_xy_chart(chart_data, config)

# plotly customizations
fig["layout"]["yaxis"]["autorange"] = "reversed"
fig.data[0].name = "Temperature"
fig.data[1].name = "Conductivity"
fig.data[2].name = "Chlorophyll"
fig.data[3].name = "Oxygen"
fig["layout"]["yaxis"]["title"] = "Pressure [PSIA]"
fig["layout"]["xaxis"]["title"] = "Temperature [ITS-90 degrees C]"
fig["layout"]["xaxis2"]["title"] = "Conductivity [S/m]"
fig["layout"]["xaxis3"]["title"] = "Chlorophyll"
fig["layout"]["xaxis4"]["title"] = "Oxygen [ml/l]"

fig.update_layout(height=800)
fig.show()